# Climate-Friendly Food Systems (CFFS) Labelling Project

### The University of British Columbia

#### Created by Silvia Huang

In [1]:
#install libraries if needed
#!pip3 install pdpipe

In [2]:
import numpy as np
import pandas as pd
import pdpipe as pdp
import matplotlib.pyplot as plt
import glob
import os
import csv
from itertools import islice
from decimal import Decimal
import xml.etree.ElementTree as et
from xml.etree.ElementTree import parse
import openpyxl
import pytest
from datetime import datetime

In [3]:
#set the root path, change the directory into the project folder
os.chdir("/Users/silvia/cffs-label")

In [4]:
#enable reading data in the scrolling window 
pd.set_option("display.max_rows", None, "display.max_columns", None)

## Import Preprocessed Datasets

In [5]:
Preps = pd.read_csv(os.path.join(os.getcwd(), "data", "cleaning", "Preps_Unit_Cleaned.csv"))
Preps.head()

PrepId                 Description  PakQty PakUOM InventoryGroup  StdQty  \
0  P-26047  BOILED|Hard Boiled Eggs FT    50.0     ea           PREP  2500.0   
1  P-58362        BRINED|Turkey|Breast     9.0     Kg           PREP  9000.0   
2  P-34084                COOKED|Bacon    20.0      g           PREP    20.0   
3  P-55141         COOKED|Charred Corn     2.0     Kg            NaN  2000.0   
4  P-48870     COOKED|Chicken Stirfry      6.3     Kg            NaN  6300.0   

  StdUom  
0      g  
1      g  
2      g  
3      g  
4      g

In [6]:
ghge_factors = pd.read_csv(os.path.join(os.getcwd(), "data", "external", "ghge_factors.csv"))
ghge_factors.head()

Category ID              Food Category  \
0            1        beef & buffalo meat   
1            2    lamb/mutton & goat meat   
2            3            pork (pig meat)   
3            4  poultry (chicken, turkey)   
4            5                     butter   

   Active Total Supply Chain Emissions (kg CO2 / kg food)  
0                                            41.3463       
1                                            41.6211       
2                                             9.8315       
3                                             4.3996       
4                                            11.4316

In [7]:
nitro_factors = pd.read_csv(os.path.join(os.getcwd(), "data", "external", "nitrogen_factors.csv"))
nitro_factors.head()

Category ID              Food Category  g N lost/kg product
0            1        beef & buffalo meat               329.50
1            2    lamb/mutton & goat meat               231.15
2            3            pork (pig meat)               132.80
3            4  poultry (chicken, turkey)               116.80
4            5                     butter               100.35

In [8]:
water_factors = pd.read_csv(os.path.join(os.getcwd(), "data", "external", "water_factors.csv"))
water_factors.head()

Category ID              Food Category  Freshwater Withdrawals (L/FU)  \
0            1        beef & buffalo meat                       1677.200   
1            2    lamb/mutton & goat meat                        461.200   
2            3            pork (pig meat)                       1810.300   
3            4  poultry (chicken, turkey)                        370.300   
4            5                     butter                       1010.176   

   Stress-Weighted Water Use (L/FU)  
0                         61309.000  
1                           258.900  
2                         54242.700  
3                           333.500  
4                         50055.168

In [9]:
# Load current Items List with assigned Emission Factors Category ID
Items_Assigned = pd.read_csv(os.path.join(os.getcwd(), "data", "mapping", "Items_List_Assigned.csv"))
Items_Assigned.head()

ItemId  CategoryID               Description  CaseQty CaseUOM  PakQty  \
0  I-57545           1   CHUCK FLAT BONELESS FZN     3.30      Kg     1.0   
1  I-10869           1       BEEF STIRFRY COV FR     5.00      Kg     1.0   
2   I-7064           1     BEEF OUTSIDE FLAT AAA     1.00      Kg     1.0   
3  I-37005           1            BEEF MEATBALLS     4.54      Kg  1000.0   
4  I-37002           1  BEEF INSIDE ROUND SHAVED     9.00      Kg  1000.0   

  PakUOM InventoryGroup  
0     Kg           MEAT  
1     Kg           MEAT  
2     Kg           MEAT  
3      g           MEAT  
4      g           MEAT

## Import Update Info

In [10]:
#import list of prep that need convert uom to standard uom manually
Manual_PrepU = pd.read_csv(os.path.join(os.getcwd(), "data", "cleaning", "Preps_UpdateUom.csv"))
Manual_PrepU.head()

PrepId                 Description  PakQty PakUOM InventoryGroup   StdQty  \
0  P-54697             LEMON|Wedge 1/8     8.0   each           PREP     84.0   
1  P-35132  MARINATED|Lemon & Herb Chx   185.0     ea           PREP  24050.0   
2  P-51992   YIELD|Bread|Sourdough 5/8    36.0  slice            NaN   1620.0   
3  P-26234  BATCH|Roasted Garlic Bread    16.0     ea           PREP   1280.0   
4  P-26170           GRILLED|NaanBread     1.0     ea           PREP    125.0   

  StdUom  
0      g  
1      g  
2      g  
3      g  
4      g

In [11]:
#select the file path for new items list with category id
New_Items_Added = pd.read_csv(os.path.join(os.getcwd(), "data", "mapping", "new items added", "New_Items_Added_6.csv"))
New_Items_Added

ItemId  CategoryID                     Description  CaseQty CaseUOM  \
0    I-58566           3                      BACON 375G        1     bag   
1     I-3962           4     CHICK DCD 1/2IN 60WHT/40DK        10      lb   
2     I-4059           4     CHICK FRYER WHLE SM GR "A"         1      Kg   
3     I-2248           5              BUTTER SALTED 454G        1    each   
4    I-17620           6           CHEESE MOZZA SLCD 14G      216   slice   
5     I-2153           6        CHEESE NACHO ECONO SHRED        2     bag   
6    I-29241           6          ICING|Cream Cheese 2KG        1     2kg   
7    I-58477           6               CB MB CHED CHEESE       16     pak   
8    I-58568           7                GELATO HOT CHOCO        8    each   
9    I-58329           7             GELATO SALT CARAMEL       12     BAR   
10    I-3802           7      ICE CREAM BJ CHERRY GARCIA        8    pail   
11   I-41442           7  ICE CREAM BJ CHOC COOKIE DOUGH        8    each   
12   I-59544           7        ICE CREAM BJ HALF BAKED         8    each   
13   I-51572           7    ICE CREAM COCONUT BLISS SAND       12     BAR   
14   I-59541           7         ICE CREAM KL STRAW KING       12      ea   
15   I-60500           7  ICE CREAM STRAW & CREAM NORA'S        8     TUB   
16   I-60501           7   ICE CREAM VANILLA BEAN NORA'S        8     TUB   
17   I-42797           7  KLONDIKE COOKIES & CREAM SANDW       24     BAR   
18   I-61562           7         MAGNUM DK CHOCO TRUFFLE       12     BAR   
19   I-34477           7     MAGNUM DOUBLE CHOCO/VANILLA       12     BAR   
20   I-34479           7   MAGNUM DOUBLE COOKIES & CREAM       12     BAR   
21   I-61513           8       CREAM CHEESE PHILLY LIGHT       12     pak   
22   I-11365           9                   MILK 2% 473ml        1      CT   
23   I-11362           9              MILK CHOC 1% 473ml        1      CT   
24   I-16330           9              MILK CHOC 1% 946ml        1      CT   
25    I-2215           9               MILK SKIM 1L -CTN        1       L   
26   I-58022          10      YOGURT 4% GREEK PLAN 450GM        6      ea   
27   I-60932          10         YOGURT BLK CHERRY 150GM       12      ea   
28   I-58333          10        YOGURT STRAW GREEK 150GM       12      ea   
29   I-58332          11                 RRF EGGS LG 6EA       30  1/2DOZ   
30    I-5048          12        SAL SOCKEYE FILLETS TRIM        1      lb   
31   I-58331          12            CAN SALMON PINK 160G       12      ea   
32   I-58570          17             AMY'S RFRD BEANS OR       12     can   
33   I-58323          20              SS TOFU FIRM 350GM        6     pak   
34   I-61314          20              SS TOFU FIRM 500GM       12     pak   
35   I-60340          20      ROLL|Inari Tofu|Retail|PKG        1      ea   
36   I-36048          21        BOB'S RED 5 Grain Rolled        4      ea   
37   I-58728          22                BOB'S CORN GRITS        4     bag   
38   I-58048          22     GRO CORN SWEET FROZEN 500GM       12     bag   
39   I-58727          23            BOB'S STEEL CUT OATS        4     bag   
40   I-13788          24             COOKIE GF CHOC CHIP       10      ea   
41    I-1109          24    CROISSANT PLAIN JUMBO U/BKD        80      CT   
42   I-56848          24  PASTRIES CHOCOLATINE PRE PROOF       60    each   
43    I-2635          24   MUFFIN BATT FRUIT EXTREME FZN       16      lb   
44    I-2636          24  MUFFIN BATT HARVEST HEALTH TFC       16      lb   
45    I-7387          24                BRIOCHE BUN 4PKG        1     pak   
46   I-11663          24       LOAF COUNTRY CRANBRY 5/8"        1    LOAF   
47   I-24225          24   LOAF ORGANIC FS PAN BIRDS & B        1   SHEET   
48   I-28236          24           LOAF SWEETHRT FS PAN        18   slice   
49   I-25290          24       SOURDOUGH CHEEKY RND FRZ         1    LOAF   
50   I-25289          24     SOURDOUGH SLCD W/W ORGANIC         1    LOAF   
51

In [12]:
#import list of items that adjusted GHGe factor manually
Manual_Factor = pd.read_csv(os.path.join(os.getcwd(), "data", "mapping", "Manual_Adjust_Factors.csv"))
Manual_Factor.head()

ItemId  CategoryID                   Description  CaseQty CaseUOM  PakQty  \
0  I-52090          59  BURGER BEEF & MUSHROOM HALAL      1.0      cs   48.00   
1  I-45558          59           Prep-Vegan Parmesan   1000.0       g    1.00   
2   I-3352          59        MAYONNAISE PAIL TFC 4L      2.0    each    4.00   
3   I-3223          59  COCONUT MILK 17/19% MILK FAT      6.0  LG CAN    2.84   
4   I-2898          59      MUSTARD DIJON WINE FLEUR      6.0     jar    1.00   

  PakUOM   InventoryGroup  \
0     CT             MEAT   
1      g  PRODUCTION FOOD   
2      L   FOOD - GROCERY   
3      L   FOOD - GROCERY   
4     Kg   FOOD - GROCERY   

   Active Total Supply Chain Emissions (kg CO2 / kg food)  \
0                                           25.00894        
1                                            3.85686        
2                                            3.55000        
3                                            3.50000        
4                                            3.32600        

   g N lost/kg product  Freshwater Withdrawals (L/FU)  \
0               200.86                        1038.84   
1                 0.00                           0.00   
2                 0.00                           0.00   
3                 0.00                           1.00   
4                 0.00                           0.00   

   Stress-Weighted Water Use (L/FU)  
0                           37961.2  
1                               0.0  
2                               0.0  
3                               1.0  
4                               0.0

### Update Correct Uom for Preps

In [13]:
#update prep list with manully adjusted uom
for index, row in Manual_PrepU.iterrows():
    PrepId = Manual_PrepU.loc[index, 'PrepId']
    qty = Manual_PrepU.loc[index, 'StdQty']
    uom = Manual_PrepU.loc[index, 'StdUom']
    Preps.loc[Preps['PrepId'] == PrepId, 'StdQty'] = qty
    Preps.loc[Preps['PrepId'] == PrepId, 'StdUom'] = uom

In [14]:
Preps.drop_duplicates(subset=['PrepId'], inplace=True,)

In [15]:
Preps.head()
Preps.shape

(43, 7)

In [16]:
path = os.path.join(os.getcwd(), "data", "cleaning", "Preps_List_Cleaned.csv")
Preps.to_csv(path, index = False, header = True)

### Import List of New Items with Emission Factors Category ID Assigned

In [17]:
frames = [Items_Assigned, New_Items_Added]
Items_Assigned_Updated = pd.concat(frames).reset_index(drop=True, inplace=False).drop_duplicates()
Items_Assigned_Updated.head()

ItemId  CategoryID               Description  CaseQty CaseUOM  PakQty  \
0  I-57545           1   CHUCK FLAT BONELESS FZN     3.30      Kg     1.0   
1  I-10869           1       BEEF STIRFRY COV FR     5.00      Kg     1.0   
2   I-7064           1     BEEF OUTSIDE FLAT AAA     1.00      Kg     1.0   
3  I-37005           1            BEEF MEATBALLS     4.54      Kg  1000.0   
4  I-37002           1  BEEF INSIDE ROUND SHAVED     9.00      Kg  1000.0   

  PakUOM InventoryGroup  
0     Kg           MEAT  
1     Kg           MEAT  
2     Kg           MEAT  
3      g           MEAT  
4      g           MEAT

In [18]:
Items_Assigned_Updated.shape

(1923, 8)

In [19]:
Items_Assigned_Updated[['CategoryID']] = Items_Assigned_Updated[['CategoryID']].apply(pd.to_numeric)

In [20]:
path = os.path.join(os.getcwd(), "data", "mapping", "Items_List_Assigned.csv")
Items_Assigned_Updated.to_csv(path, index = False, header = True)

## Mapping Items to Footprint Factors

In [21]:
# map GHG footprint factors
mapping = pd.merge(Items_Assigned_Updated, ghge_factors.loc[:,['Category ID','Food Category','Active Total Supply Chain Emissions (kg CO2 / kg food)']], 
                  how = 'left',
                  left_on = 'CategoryID', 
                  right_on = 'Category ID')
for index in mapping.index:
    if np.isnan(mapping.loc[index,'Category ID']):
        mapping.loc[index,'Active Total Supply Chain Emissions (kg CO2 / kg food)'] = 0

mapping = mapping.drop(columns=['Category ID', 'Food Category'])
mapping

ItemId  CategoryID                     Description    CaseQty  CaseUOM  \
0     I-57545           1         CHUCK FLAT BONELESS FZN      3.300       Kg   
1     I-10869           1             BEEF STIRFRY COV FR      5.000       Kg   
2      I-7064           1           BEEF OUTSIDE FLAT AAA      1.000       Kg   
3     I-37005           1                  BEEF MEATBALLS      4.540       Kg   
4     I-37002           1        BEEF INSIDE ROUND SHAVED      9.000       Kg   
5      I-3876           1           BEEF CHUCK GROUND AAA      1.000       Kg   
6     I-34065           1           BEEF BONES KNUCKLE FZ      1.000       Kg   
7     I-11661           1           BEEF STEW 3/4" FROZEN      5.000       Kg   
8      I-3837           1          BEEF STEW DICED 3/4"FR      1.000       Kg   
9     I-43648           1       BRISKET BEEF CORN SMKD FR      4.500       Kg   
10     I-3838           1      BEEF BRISKET BNLS 3/4" AAA      1.000       Kg   
11    I-49128           1       HOT DOG BEEF G/FREE 6 INC     10.000       lb   
12    I-17055           1   BEEF RIB BRAISING 3 BONE 1/4"      1.000       Kg   
13    I-13303           3            SAUSAGE PATTIES PORK      5.000       Kg   
14    I-11922           3       SAUSAGE MEAT CHORIZO FRZN      5.000       CT   
15    I-50575           3    SAUSAGE ITAL CRUMBLE CKD FRZ      2.000      bag   
16     I-2317           3    SAUSAGE FARMER DOUBLE SMOKED      1.000       Kg   
17    I-17667           3            SAUSAGE CHORIZO MEAT      5.000       Kg   
18     I-2333           3   PROSCIUTTO SLICED SAN DANIELE      1.000       Kg   
19     I-6869           3  PROSCIUTTO COTTO MASTRO SLICED      1.000       Kg   
20     I-3856           3      PORK LOIN BNLS S/CUT COVFR      1.000       Kg   
21     I-3887           3       PORK GROUND BRITCO PER KG      1.000       Kg   
22     I-3855           3                   PORK GRD FRZ       5.000       Kg   
23     I-3851           3       PORK BUTT BNLS 1/4 COV FR      1.000       Kg   
24     I-2311           3            HAM PROSCIUTTO BNLS       1.000       Kg   
25     I-2310           3                      HAM HONEY       6.000      pak   
26     I-2306           3            HAM BLACK FOREST slc      6.000      pak   
27     I-8260           3       CAPICOLLO EXT HOT CAPOLLA      1.000       Kg   
28    I-27410           3        BACON 3MM NATURALLY SMKD      5.000       Kg   
29     I-2308           3                 HAM CAPICOLLIFR      1.000       Kg   
30     I-2305           3                  BACON PANCETTA      1.000       Kg   
31    I-13423           3                   PORK STIR FRY      5.000       Kg   
32    I-19657           3               SAUSAGE ANDOUILLE      5.000       Kg   
33     I-2319           3         SMOKIES 5.5 CT BAVARIAN      1.000       Kg   
34    I-42350           3       PORK BACK RIB 1/2 RACK FZ      1.000       Kg   
35     I-3853           3              PORK CHOP 170G C/C     28.000       CT   
36     I-8140           3            SAUSAGE CHORIZO WINE      1.000       Kg   
37    I-57497           3  SAUSAGE FRANKFURTER FLD ROAST      12.000      pak   
38    I-22916           3             PORK BELLY SKON COV      1.000       Kg   
39    I-57496           3    SAUSAGE SMKD APPLE FLD ROAST     12.000      pak   
40     I-3854           3           PORK CUTLET 115G BRD      40.000       CT   
41    I-27407           4        TURKEY SAUSAGE BREAKFAST     20.000       ea   
42     I-7065           4     TURKEY RST COMBO SURE SLICE      1.000       Kg   
43     I-3983           4   CHICKEN BREAST BONELESS FRESH      1.000       Kg   
44     I-8363           4    CHICK WINGS SPLT FRESH HALAL      1.000       Kg   
45    I-19665           4       CHICK THIGH STIRFRY HALAL      1.000       Kg   
46     I-4016           4     CHICK THIGH DICED HALAL 1"       1.000       Kg   
47     I-4010           4       CHICK THIGH BONE IN HALAL      1.000       Kg   
48     I-4008           4            C

In [22]:
# map nitrogen footprint factors
mapping = pd.merge(mapping, nitro_factors.loc[:,['Category ID','Food Category','g N lost/kg product']], 
                  how = 'left',
                  left_on = 'CategoryID', 
                  right_on = 'Category ID')

for index in mapping.index:
    if np.isnan(mapping.loc[index,'Category ID']):
        mapping.loc[index,'g N lost/kg product'] = 0

mapping = mapping.drop(columns=['Category ID', 'Food Category'])
mapping

ItemId  CategoryID                     Description    CaseQty  CaseUOM  \
0     I-57545           1         CHUCK FLAT BONELESS FZN      3.300       Kg   
1     I-10869           1             BEEF STIRFRY COV FR      5.000       Kg   
2      I-7064           1           BEEF OUTSIDE FLAT AAA      1.000       Kg   
3     I-37005           1                  BEEF MEATBALLS      4.540       Kg   
4     I-37002           1        BEEF INSIDE ROUND SHAVED      9.000       Kg   
5      I-3876           1           BEEF CHUCK GROUND AAA      1.000       Kg   
6     I-34065           1           BEEF BONES KNUCKLE FZ      1.000       Kg   
7     I-11661           1           BEEF STEW 3/4" FROZEN      5.000       Kg   
8      I-3837           1          BEEF STEW DICED 3/4"FR      1.000       Kg   
9     I-43648           1       BRISKET BEEF CORN SMKD FR      4.500       Kg   
10     I-3838           1      BEEF BRISKET BNLS 3/4" AAA      1.000       Kg   
11    I-49128           1       HOT DOG BEEF G/FREE 6 INC     10.000       lb   
12    I-17055           1   BEEF RIB BRAISING 3 BONE 1/4"      1.000       Kg   
13    I-13303           3            SAUSAGE PATTIES PORK      5.000       Kg   
14    I-11922           3       SAUSAGE MEAT CHORIZO FRZN      5.000       CT   
15    I-50575           3    SAUSAGE ITAL CRUMBLE CKD FRZ      2.000      bag   
16     I-2317           3    SAUSAGE FARMER DOUBLE SMOKED      1.000       Kg   
17    I-17667           3            SAUSAGE CHORIZO MEAT      5.000       Kg   
18     I-2333           3   PROSCIUTTO SLICED SAN DANIELE      1.000       Kg   
19     I-6869           3  PROSCIUTTO COTTO MASTRO SLICED      1.000       Kg   
20     I-3856           3      PORK LOIN BNLS S/CUT COVFR      1.000       Kg   
21     I-3887           3       PORK GROUND BRITCO PER KG      1.000       Kg   
22     I-3855           3                   PORK GRD FRZ       5.000       Kg   
23     I-3851           3       PORK BUTT BNLS 1/4 COV FR      1.000       Kg   
24     I-2311           3            HAM PROSCIUTTO BNLS       1.000       Kg   
25     I-2310           3                      HAM HONEY       6.000      pak   
26     I-2306           3            HAM BLACK FOREST slc      6.000      pak   
27     I-8260           3       CAPICOLLO EXT HOT CAPOLLA      1.000       Kg   
28    I-27410           3        BACON 3MM NATURALLY SMKD      5.000       Kg   
29     I-2308           3                 HAM CAPICOLLIFR      1.000       Kg   
30     I-2305           3                  BACON PANCETTA      1.000       Kg   
31    I-13423           3                   PORK STIR FRY      5.000       Kg   
32    I-19657           3               SAUSAGE ANDOUILLE      5.000       Kg   
33     I-2319           3         SMOKIES 5.5 CT BAVARIAN      1.000       Kg   
34    I-42350           3       PORK BACK RIB 1/2 RACK FZ      1.000       Kg   
35     I-3853           3              PORK CHOP 170G C/C     28.000       CT   
36     I-8140           3            SAUSAGE CHORIZO WINE      1.000       Kg   
37    I-57497           3  SAUSAGE FRANKFURTER FLD ROAST      12.000      pak   
38    I-22916           3             PORK BELLY SKON COV      1.000       Kg   
39    I-57496           3    SAUSAGE SMKD APPLE FLD ROAST     12.000      pak   
40     I-3854           3           PORK CUTLET 115G BRD      40.000       CT   
41    I-27407           4        TURKEY SAUSAGE BREAKFAST     20.000       ea   
42     I-7065           4     TURKEY RST COMBO SURE SLICE      1.000       Kg   
43     I-3983           4   CHICKEN BREAST BONELESS FRESH      1.000       Kg   
44     I-8363           4    CHICK WINGS SPLT FRESH HALAL      1.000       Kg   
45    I-19665           4       CHICK THIGH STIRFRY HALAL      1.000       Kg   
46     I-4016           4     CHICK THIGH DICED HALAL 1"       1.000       Kg   
47     I-4010           4       CHICK THIGH BONE IN HALAL      1.000       Kg   
48     I-4008           4            C

In [23]:
# map water footprint factors
mapping = pd.merge(mapping, water_factors.loc[:,['Category ID','Food Category','Freshwater Withdrawals (L/FU)', 'Stress-Weighted Water Use (L/FU)']], 
                  how = 'left',
                  left_on = 'CategoryID', 
                  right_on = 'Category ID')

for index in mapping.index:
    if np.isnan(mapping.loc[index,'Category ID']):
        mapping.loc[index,'Freshwater Withdrawals (L/FU)'] = 0
        mapping.loc[index,'Stress-Weighted Water Use (L/FU)'] = 0

mapping = mapping.drop(columns=['Category ID', 'Food Category'])
mapping

ItemId  CategoryID                     Description    CaseQty  CaseUOM  \
0     I-57545           1         CHUCK FLAT BONELESS FZN      3.300       Kg   
1     I-10869           1             BEEF STIRFRY COV FR      5.000       Kg   
2      I-7064           1           BEEF OUTSIDE FLAT AAA      1.000       Kg   
3     I-37005           1                  BEEF MEATBALLS      4.540       Kg   
4     I-37002           1        BEEF INSIDE ROUND SHAVED      9.000       Kg   
5      I-3876           1           BEEF CHUCK GROUND AAA      1.000       Kg   
6     I-34065           1           BEEF BONES KNUCKLE FZ      1.000       Kg   
7     I-11661           1           BEEF STEW 3/4" FROZEN      5.000       Kg   
8      I-3837           1          BEEF STEW DICED 3/4"FR      1.000       Kg   
9     I-43648           1       BRISKET BEEF CORN SMKD FR      4.500       Kg   
10     I-3838           1      BEEF BRISKET BNLS 3/4" AAA      1.000       Kg   
11    I-49128           1       HOT DOG BEEF G/FREE 6 INC     10.000       lb   
12    I-17055           1   BEEF RIB BRAISING 3 BONE 1/4"      1.000       Kg   
13    I-13303           3            SAUSAGE PATTIES PORK      5.000       Kg   
14    I-11922           3       SAUSAGE MEAT CHORIZO FRZN      5.000       CT   
15    I-50575           3    SAUSAGE ITAL CRUMBLE CKD FRZ      2.000      bag   
16     I-2317           3    SAUSAGE FARMER DOUBLE SMOKED      1.000       Kg   
17    I-17667           3            SAUSAGE CHORIZO MEAT      5.000       Kg   
18     I-2333           3   PROSCIUTTO SLICED SAN DANIELE      1.000       Kg   
19     I-6869           3  PROSCIUTTO COTTO MASTRO SLICED      1.000       Kg   
20     I-3856           3      PORK LOIN BNLS S/CUT COVFR      1.000       Kg   
21     I-3887           3       PORK GROUND BRITCO PER KG      1.000       Kg   
22     I-3855           3                   PORK GRD FRZ       5.000       Kg   
23     I-3851           3       PORK BUTT BNLS 1/4 COV FR      1.000       Kg   
24     I-2311           3            HAM PROSCIUTTO BNLS       1.000       Kg   
25     I-2310           3                      HAM HONEY       6.000      pak   
26     I-2306           3            HAM BLACK FOREST slc      6.000      pak   
27     I-8260           3       CAPICOLLO EXT HOT CAPOLLA      1.000       Kg   
28    I-27410           3        BACON 3MM NATURALLY SMKD      5.000       Kg   
29     I-2308           3                 HAM CAPICOLLIFR      1.000       Kg   
30     I-2305           3                  BACON PANCETTA      1.000       Kg   
31    I-13423           3                   PORK STIR FRY      5.000       Kg   
32    I-19657           3               SAUSAGE ANDOUILLE      5.000       Kg   
33     I-2319           3         SMOKIES 5.5 CT BAVARIAN      1.000       Kg   
34    I-42350           3       PORK BACK RIB 1/2 RACK FZ      1.000       Kg   
35     I-3853           3              PORK CHOP 170G C/C     28.000       CT   
36     I-8140           3            SAUSAGE CHORIZO WINE      1.000       Kg   
37    I-57497           3  SAUSAGE FRANKFURTER FLD ROAST      12.000      pak   
38    I-22916           3             PORK BELLY SKON COV      1.000       Kg   
39    I-57496           3    SAUSAGE SMKD APPLE FLD ROAST     12.000      pak   
40     I-3854           3           PORK CUTLET 115G BRD      40.000       CT   
41    I-27407           4        TURKEY SAUSAGE BREAKFAST     20.000       ea   
42     I-7065           4     TURKEY RST COMBO SURE SLICE      1.000       Kg   
43     I-3983           4   CHICKEN BREAST BONELESS FRESH      1.000       Kg   
44     I-8363           4    CHICK WINGS SPLT FRESH HALAL      1.000       Kg   
45    I-19665           4       CHICK THIGH STIRFRY HALAL      1.000       Kg   
46     I-4016           4     CHICK THIGH DICED HALAL 1"       1.000       Kg   
47     I-4010           4       CHICK THIGH BONE IN HALAL      1.000       Kg   
48     I-4008           4            C

### Manully Adjust Footprint Factor for Specific Items

In [24]:
for index, row in Manual_Factor.iterrows():
    itemId = Manual_Factor.loc[index, 'ItemId']
    ghge = Manual_Factor.loc[index, 'Active Total Supply Chain Emissions (kg CO2 / kg food)']
    nitro = Manual_Factor.loc[index, 'g N lost/kg product']
    water = Manual_Factor.loc[index, 'Freshwater Withdrawals (L/FU)']
    str_water = Manual_Factor.loc[index, 'Stress-Weighted Water Use (L/FU)']
    mapping.loc[mapping['ItemId'] == itemId, 'Active Total Supply Chain Emissions (kg CO2 / kg food)'] = ghge
    mapping.loc[mapping['ItemId'] == itemId, 'g N lost/kg product'] = nitro
    mapping.loc[mapping['ItemId'] == itemId, 'Freshwater Withdrawals (L/FU)'] = water
    mapping.loc[mapping['ItemId'] == itemId, 'Stress-Weighted Water Use (L/FU)'] = str_water

In [25]:
mapping.drop_duplicates(subset = ['ItemId'], inplace=True)
mapping.shape
mapping.dtypes

ItemId                                                     object
CategoryID                                                  int64
Description                                                object
CaseQty                                                   float64
CaseUOM                                                    object
PakQty                                                    float64
PakUOM                                                     object
InventoryGroup                                             object
Active Total Supply Chain Emissions (kg CO2 / kg food)    float64
g N lost/kg product                                       float64
Freshwater Withdrawals (L/FU)                             float64
Stress-Weighted Water Use (L/FU)                          float64
dtype: object

In [26]:
mapping

ItemId  CategoryID                     Description    CaseQty  CaseUOM  \
0     I-57545           1         CHUCK FLAT BONELESS FZN      3.300       Kg   
1     I-10869           1             BEEF STIRFRY COV FR      5.000       Kg   
2      I-7064           1           BEEF OUTSIDE FLAT AAA      1.000       Kg   
3     I-37005           1                  BEEF MEATBALLS      4.540       Kg   
4     I-37002           1        BEEF INSIDE ROUND SHAVED      9.000       Kg   
5      I-3876           1           BEEF CHUCK GROUND AAA      1.000       Kg   
6     I-34065           1           BEEF BONES KNUCKLE FZ      1.000       Kg   
7     I-11661           1           BEEF STEW 3/4" FROZEN      5.000       Kg   
8      I-3837           1          BEEF STEW DICED 3/4"FR      1.000       Kg   
9     I-43648           1       BRISKET BEEF CORN SMKD FR      4.500       Kg   
10     I-3838           1      BEEF BRISKET BNLS 3/4" AAA      1.000       Kg   
11    I-49128           1       HOT DOG BEEF G/FREE 6 INC     10.000       lb   
12    I-17055           1   BEEF RIB BRAISING 3 BONE 1/4"      1.000       Kg   
13    I-13303           3            SAUSAGE PATTIES PORK      5.000       Kg   
14    I-11922           3       SAUSAGE MEAT CHORIZO FRZN      5.000       CT   
15    I-50575           3    SAUSAGE ITAL CRUMBLE CKD FRZ      2.000      bag   
16     I-2317           3    SAUSAGE FARMER DOUBLE SMOKED      1.000       Kg   
17    I-17667           3            SAUSAGE CHORIZO MEAT      5.000       Kg   
18     I-2333           3   PROSCIUTTO SLICED SAN DANIELE      1.000       Kg   
19     I-6869           3  PROSCIUTTO COTTO MASTRO SLICED      1.000       Kg   
20     I-3856           3      PORK LOIN BNLS S/CUT COVFR      1.000       Kg   
21     I-3887           3       PORK GROUND BRITCO PER KG      1.000       Kg   
22     I-3855           3                   PORK GRD FRZ       5.000       Kg   
23     I-3851           3       PORK BUTT BNLS 1/4 COV FR      1.000       Kg   
24     I-2311           3            HAM PROSCIUTTO BNLS       1.000       Kg   
25     I-2310           3                      HAM HONEY       6.000      pak   
26     I-2306           3            HAM BLACK FOREST slc      6.000      pak   
27     I-8260           3       CAPICOLLO EXT HOT CAPOLLA      1.000       Kg   
28    I-27410           3        BACON 3MM NATURALLY SMKD      5.000       Kg   
29     I-2308           3                 HAM CAPICOLLIFR      1.000       Kg   
30     I-2305           3                  BACON PANCETTA      1.000       Kg   
31    I-13423           3                   PORK STIR FRY      5.000       Kg   
32    I-19657           3               SAUSAGE ANDOUILLE      5.000       Kg   
33     I-2319           3         SMOKIES 5.5 CT BAVARIAN      1.000       Kg   
34    I-42350           3       PORK BACK RIB 1/2 RACK FZ      1.000       Kg   
35     I-3853           3              PORK CHOP 170G C/C     28.000       CT   
36     I-8140           3            SAUSAGE CHORIZO WINE      1.000       Kg   
37    I-57497           3  SAUSAGE FRANKFURTER FLD ROAST      12.000      pak   
38    I-22916           3             PORK BELLY SKON COV      1.000       Kg   
39    I-57496           3    SAUSAGE SMKD APPLE FLD ROAST     12.000      pak   
40     I-3854           3           PORK CUTLET 115G BRD      40.000       CT   
41    I-27407           4        TURKEY SAUSAGE BREAKFAST     20.000       ea   
42     I-7065           4     TURKEY RST COMBO SURE SLICE      1.000       Kg   
43     I-3983           4   CHICKEN BREAST BONELESS FRESH      1.000       Kg   
44     I-8363           4    CHICK WINGS SPLT FRESH HALAL      1.000       Kg   
45    I-19665           4       CHICK THIGH STIRFRY HALAL      1.000       Kg   
46     I-4016           4     CHICK THIGH DICED HALAL 1"       1.000       Kg   
47     I-4010           4       CHICK THIGH BONE IN HALAL      1.000       Kg   
48     I-4008           4            C

In [27]:
path = os.path.join(os.getcwd(), "data", "mapping", "Mapping.csv")
mapping.to_csv(path, index = False, header = True)